In [1]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import numpy as np
from sklearn.preprocessing import MinMaxScaler

In [2]:
df_train = pd.read_csv('../../data/train.csv')
print(f'Dimensions of DataFrame: {df_train.shape}')
df_train.head(5)

Dimensions of DataFrame: (3000888, 6)


id        date  store_nbr      family  sales  onpromotion
0   0  2013-01-01          1  AUTOMOTIVE    0.0            0
1   1  2013-01-01          1   BABY CARE    0.0            0
2   2  2013-01-01          1      BEAUTY    0.0            0
3   3  2013-01-01          1   BEVERAGES    0.0            0
4   4  2013-01-01          1       BOOKS    0.0            0

In [3]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000888 entries, 0 to 3000887
Data columns (total 6 columns):
 #   Column       Dtype  
---  ------       -----  
 0   id           int64  
 1   date         object 
 2   store_nbr    int64  
 3   family       object 
 4   sales        float64
 5   onpromotion  int64  
dtypes: float64(1), int64(3), object(2)
memory usage: 137.4+ MB


In [4]:
# Change type of columns
df_train['date'] = pd.to_datetime(df_train['date'])
df_train['family'] = df_train['family'].astype(str)

In [5]:
df_test = pd.read_csv('../../data/test.csv')
print(f'Dimensions of DataFrame: {df_test.shape}')
df_test.head(5)

Dimensions of DataFrame: (28512, 5)


id        date  store_nbr      family  onpromotion
0  3000888  2017-08-16          1  AUTOMOTIVE            0
1  3000889  2017-08-16          1   BABY CARE            0
2  3000890  2017-08-16          1      BEAUTY            2
3  3000891  2017-08-16          1   BEVERAGES           20
4  3000892  2017-08-16          1       BOOKS            0

In [6]:
df_test['date'] = pd.to_datetime(df_test['date'])
df_test['family'] = df_test['family'].astype(str)

We have to predict for each of the ids the number of sales

In [6]:
n_families = len(df_train['family'].unique())
print(f"There are {n_families} different families")

There are 33 different families


In [7]:
df_train_1 = df_train.loc[df_train['store_nbr'] == 1]
fig = px.line(df_train_1, x = 'date', y = 'sales', color = 'family')
fig.show()

We can appreciate that the time series aren't in the same scale, and that some families don't have any sale (BABY CARE).

We also can appreciate that the majority of families have weekly cycles.

Some of the families have periods without any sale and outliers:
- Books (any sale since mid 2016)
- Celebration (periods without any sale and an outlier in mid 2014)
- Frozen Foods (outlier in finals of 2015)
- Home and Kitchen I (outlier in beginning of 2016)
- Home and Kitchen II (periods without sales)
- Home Appliances (periods without sales and outlier mid 2016)
- Home Care (periods without sales)
- Ladieswear (periods without sales)
- Magazines (periods without sales)
- Personal Care (outliers mid 2016 and beginning 2017)
- Pet supplies (Periods without sales)
- Players and electronics (Periods without sales)
- Produce (Periods without sales)
- School and Office Supplies (Periods without sales)

In [8]:
# To observe better the histogram we scale it
df_scale = df_train_1.pivot(columns = 'family', values = 'sales', index = ['date', 'store_nbr'])
scaler = MinMaxScaler()
scaled_data = scaler.fit_transform(df_scale)
df_scale = pd.DataFrame(scaled_data, index = df_scale.index, columns = df_scale.columns).reset_index()
df_scale = pd.melt(df_scale, id_vars=['date', 'store_nbr'], var_name='family', value_name='sales')
fig = px.histogram(df_scale, x = 'sales', color = 'family')
fig.show()

Here we can appreciate the number of data that is missing in the store 1 (majority of data in the firt bin)

In [9]:
# Weekly seasonality
fig = go.Figure()
max_flag = 15
for family in ['MAGAZINES', 'MEATS', 'PREPARED FOODS']:
    df_family = df_train_1.loc[df_train_1['family'] == family]
    # Compute ACF (autocorrelation)
    acf = [df_family['sales'].autocorr(i) for i in range(1,max_flag)]
    fig.add_trace(go.Bar(x = list(range(1,max_flag)), y = acf, name = family))
fig.show()

We can see that some families have weekly stationality (PREPARED FOODS and MEATS) and some not

In [11]:
# Data processing of outliers and missing periods
# Outliers -> Average
# Missing periods -> Inerpolate except if the missing period is in the beginning, then drop

In [10]:
n_stores = len(df_train['store_nbr'].unique())
print(f"There are {n_stores} different stores")

There are 54 different stores


In [11]:
# Do all the stores have the same families?
df_families = df_train.groupby(by = ['family'], as_index=False)['store_nbr'].nunique()
df_families.columns = ['family', 'number_stores']
fig = px.bar(df_families, x = 'family', y = 'number_stores')
fig.show()

We can see that all of the families are in the 54 stores

In [12]:
print(f"If we do one model for each tuple store-family, we have a total of {n_stores * n_families} models")

If we do one model for each tuple store-family, we have a total of 1782 models


In [14]:
init_test = df_test['date'].min()
fin_test = df_test['date'].max()
print(f"Test DataFrame goes from {init_test} to {fin_test}")

Test DataFrame goes from 2017-08-16 to 2017-08-31


We only have 15 days of testing

## ADDITIONAL DATASETS

### OIL

In [15]:
df_oil = pd.read_csv("../../data/oil.csv")
df_oil.head(5) # Price of the oil during training and testing

date  dcoilwtico
0  2013-01-01         NaN
1  2013-01-02       93.14
2  2013-01-03       92.97
3  2013-01-04       93.12
4  2013-01-07       93.20

In [16]:
fig = px.line(df_oil, x = 'date', y = 'dcoilwtico')
fig.show()

We can observate that some data is missing

In [17]:
print("Percentage of NaN: ", 100*df_oil['dcoilwtico'].isna().sum()/len(df_oil))

Percentage of NaN:  3.5303776683087027


### STORES

In [18]:
df_stores = pd.read_csv('../../data/stores.csv')
df_stores.head(5)

store_nbr           city                           state type  cluster
0          1          Quito                       Pichincha    D       13
1          2          Quito                       Pichincha    D       13
2          3          Quito                       Pichincha    D        8
3          4          Quito                       Pichincha    D        9
4          5  Santo Domingo  Santo Domingo de los Tsachilas    D        4

Cluster is a grouping of similar stores

In [19]:
df_stores['city'].value_counts()

city
Quito            18
Guayaquil         8
Cuenca            3
Santo Domingo     3
Manta             2
Latacunga         2
Machala           2
Ambato            2
Quevedo           1
Esmeraldas        1
Loja              1
Libertad          1
Playas            1
Daule             1
Babahoyo          1
Salinas           1
Puyo              1
Guaranda          1
Ibarra            1
Riobamba          1
Cayambe           1
El Carmen         1
Name: count, dtype: int64

In [20]:
df_stores['state'].value_counts()

state
Pichincha                         19
Guayas                            11
Santo Domingo de los Tsachilas     3
Azuay                              3
Manabi                             3
Cotopaxi                           2
Tungurahua                         2
Los Rios                           2
El Oro                             2
Chimborazo                         1
Imbabura                           1
Bolivar                            1
Pastaza                            1
Santa Elena                        1
Loja                               1
Esmeraldas                         1
Name: count, dtype: int64

In [21]:
pd.crosstab(df_stores['type'], df_stores['cluster'])

cluster  1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17
type                                                                       
A         0   0   0   0   1   0   0   0   0   0   3   0   0   4   0   0   1
B         0   0   0   0   0   6   0   0   0   1   0   0   0   0   0   1   0
C         0   0   7   0   0   0   2   0   0   0   0   1   0   0   5   0   0
D         3   2   0   3   0   0   0   3   2   1   0   0   4   0   0   0   0
E         0   0   0   0   0   0   0   0   0   4   0   0   0   0   0   0   0

We can see that each cluster only have one type of stores except the cluster 10

### HOLIDAYS

In [22]:
df_holidays = pd.read_csv('../../data/holidays_events.csv')
df_holidays.head(5)

date     type    locale locale_name                    description  \
0  2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1  2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2  2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3  2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4  2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   

   transferred  
0        False  
1        False  
2        False  
3        False  
4        False

A holiday that is transferred officially falls on that calendar day, but was moved to another date by the government. A transferred day is more like a normal day than a holiday. To find the day that it was actually celebrated, look for the corresponding row where type is Transfer.

In [23]:
df_holidays.shape

(350, 6)

In [24]:
df_holidays['locale'].value_counts()

locale
National    174
Local       152
Regional     24
Name: count, dtype: int64

In [25]:
df_holidays.loc[df_holidays['locale'] == 'Regional']['locale_name'].unique()

array(['Cotopaxi', 'Imbabura', 'Santo Domingo de los Tsachilas',
       'Santa Elena'], dtype=object)

We can see that the regions are equivalent to the state level of the stores

In [26]:
df_holidays['type'].value_counts()

type
Holiday       221
Event          56
Additional     51
Transfer       12
Bridge          5
Work Day        5
Name: count, dtype: int64

### TRANSACTIONS

In [27]:
df_transactions = pd.read_csv('../../data/transactions.csv')
df_transactions.head(5)

date  store_nbr  transactions
0  2013-01-01         25           770
1  2013-01-02          1          2111
2  2013-01-02          2          2358
3  2013-01-02          3          3487
4  2013-01-02          4          1922

It seems that this table contains the number of sells aggregating all the families. But for the day one some stores are missing